#Databricks with Python demo

This notebook is based on the following offical databricks notebook: https://docs.databricks.com/spark/latest/mllib/binary-classification-mllib-pipelines.html

## Getting and transforming the data

In this demo, we will use the adult data, which is a sample dataset included in databricks. We will read in the data in SQL using the CSV data source for Spark.

In [3]:
%sql
CREATE TABLE adult (
  age DOUBLE,
  workclass STRING,
  fnlwgt DOUBLE,
  education STRING,
  education_num DOUBLE,
  marital_status STRING,
  occupation STRING,
  relationship STRING,
  race STRING,
  sex STRING,
  capital_gain DOUBLE,
  capital_loss DOUBLE,
  hours_per_week DOUBLE,
  native_country STRING,
  income STRING)
USING CSV
OPTIONS (path "/databricks-datasets/adult/adult.data", header "true")

com.databricks.backend.common.rpc.DatabricksExceptions$SQLExecutionException: org.apache.spark.sql.AnalysisException: Table adult already exists.;
	at org.apache.spark.sql.execution.command.CreateDataSourceTableCommand.run(createDataSourceTables.scala:56)
	at org.apache.spark.sql.execution.command.ExecutedCommandExec.sideEffectResult$lzycompute(commands.scala:72)
	at org.apache.spark.sql.execution.command.ExecutedCommandExec.sideEffectResult(commands.scala:70)
	at org.apache.spark.sql.execution.command.ExecutedCommandExec.executeCollect(commands.scala:81)
	at org.apache.spark.sql.Dataset$$anonfun$6.apply(Dataset.scala:205)
	at org.apache.spark.sql.Dataset$$anonfun$6.apply(Dataset.scala:205)
	at org.apache.spark.sql.Dataset$$anonfun$54.apply(Dataset.scala:3430)
	at org.apache.spark.sql.Dataset$$anonfun$54.apply(Dataset.scala:3425)
	at org.apache.spark.sql.execution.SQLExecution$$anonfun$withCustomExecutionEnv$1.apply(SQLExecution.scala:111)
	at org.apache.spark.sql.execution.SQLExecution$.withSQLConfPropagated(SQLExecution.scala:240)
	at org.apache.spark.sql.execution.SQLExecution$.withCustomExecutionEnv(SQLExecution.scala:97)
	at org.apache.spark.sql.execution.SQLExecution$.withNewExecutionId(SQLExecution.scala:170)
	at org.apache.spark.sql.Dataset.org$apache$spark$sql$Dataset$$withAction(Dataset.scala:3425)
	at org.apache.spark.sql.Dataset. (Dataset.scala:205)
	at org.apache.spark.sql.Dataset$.ofRows(Dataset.scala:89)
	at org.apache.spark.sql.SparkSession.sql(SparkSession.scala:696)
	at org.apache.spark.sql.SQLContext.sql(SQLContext.scala:716)
	at com.databricks.backend.daemon.driver.SQLDriverLocal$$anonfun$1.apply(SQLDriverLocal.scala:88)
	at com.databricks.backend.daemon.driver.SQLDriverLocal$$anonfun$1.apply(SQLDriverLocal.scala:34)
	at scala.collection.TraversableLike$$anonfun$map$1.apply(TraversableLike.scala:234)
	at scala.collection.TraversableLike$$anonfun$map$1.apply(TraversableLike.scala:234)
	at scala.collection.immutable.List.foreach(List.scala:392)
	at scala.collection.TraversableLike$class.map(TraversableLike.scala:234)
	at scala.collection.immutable.List.map(List.scala:296)
	at com.databricks.backend.daemon.driver.SQLDriverLocal.executeSql(SQLDriverLocal.scala:34)
	at com.databricks.backend.daemon.driver.SQLDriverLocal.repl(SQLDriverLocal.scala:141)
	at com.databricks.backend.daemon.driver.DriverLocal$$anonfun$execute$8.apply(DriverLocal.scala:368)
	at com.databricks.backend.daemon.driver.DriverLocal$$anonfun$execute$8.apply(DriverLocal.scala:345)
	at com.databricks.logging.UsageLogging$$anonfun$withAttributionContext$1.apply(UsageLogging.scala:238)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:58)
	at com.databricks.logging.UsageLogging$class.withAttributionContext(UsageLogging.scala:233)
	at com.databricks.backend.daemon.driver.DriverLocal.withAttributionContext(DriverLocal.scala:48)
	at com.databricks.logging.UsageLogging$class.withAttributionTags(UsageLogging.scala:271)
	at com.databricks.backend.daemon.driver.DriverLocal.withAttributionTags(DriverLocal.scala:48)
	at com.databricks.backend.daemon.driver.DriverLocal.execute(DriverLocal.scala:345)
	at com.databricks.backend.daemon.driver.DriverWrapper$$anonfun$tryExecutingCommand$2.apply(DriverWrapper.scala:644)
	at com.databricks.backend.daemon.driver.DriverWrapper$$anonfun$tryExecutingCommand$2.apply(DriverWrapper.scala:644)
	at scala.util.Try$.apply(Try.scala:192)
	at com.databricks.backend.daemon.driver.DriverWrapper.tryExecutingCommand(DriverWrapper.scala:639)
	at com.databricks.backend.daemon.driver.DriverWrapper.getCommandOutputAndError(DriverWrapper.scala:485)
	at com.databricks.backend.daemon.driver.DriverWrapper.executeCommand(DriverWrapper.scala:597)
	at com.databricks.backend.daemon.driver.DriverWrapper.runInnerLoop(DriverWrapper.scala:390)
	at com.databricks.backend.daemon.driver.DriverWrapper.runInner(DriverWrapper.scala:337)
	at com.databricks.backend.daemon.driver.DriverWrapper.run(DriverWrapper.scala:219)
	at java.lang.Thread

In [4]:
sparkdf = spark.table("adult")
display(sparkdf)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income 50.0 Self-emp-not-inc 83311.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 13.0 United-States <=50K 38.0 Private 215646.0 HS-grad 9.0 Divorced Handlers-cleaners Not-in-family White Male 0.0 0.0 40.0 United-States <=50K 53.0 Private 234721.0 11th 7.0 Married-civ-spouse Handlers-cleaners Husband Black Male 0.0 0.0 40.0 United-States <=50K 28.0 Private 338409.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Wife Black Female 0.0 0.0 40.0 Cuba <=50K 37.0 Private 284582.0 Masters 14.0 Married-civ-spouse Exec-managerial Wife White Female 0.0 0.0 40.0 United-States <=50K 49.0 Private 160187.0 9th 5.0 Married-spouse-absent Other-service Not-in-family Black Female 0.0 0.0 16.0 Jamaica <=50K 52.0 Self-emp-not-inc 209642.0 HS-grad 9.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 45.0 United-States >50K 31.0 Private 45781.0 Masters 14.0 Never-married Prof-specialty Not-in-family White Female 14084.0 0.0 50.0 United-States >50K 42.0 Private 159449.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 5178.0 0.0 40.0 United-States >50K 37.0 Private 280464.0 Some-college 10.0 Married-civ-spouse Exec-managerial Husband Black Male 0.0 0.0 80.0 United-States >50K 30.0 State-gov 141297.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Husband Asian-Pac-Islander Male 0.0 0.0 40.0 India >50K 23.0 Private 122272.0 Bachelors 13.0 Never-married Adm-clerical Own-child White Female 0.0 0.0 30.0 United-States <=50K 32.0 Private 205019.0 Assoc-acdm 12.0 Never-married Sales Not-in-family Black Male 0.0 0.0 50.0 United-States <=50K 40.0 Private 121772.0 Assoc-voc 11.0 Married-civ-spouse Craft-repair Husband Asian-Pac-Islander Male 0.0 0.0 40.0 ? >50K 34.0 Private 245487.0 7th-8th 4.0 Married-civ-spouse Transport-moving Husband Amer-Indian-Eskimo Male 0.0 0.0 45.0 Mexico <=50K 25.0 Self-emp-not-inc 176756.0 HS-grad 9.0 Never-married Farming-fishing Own-child White Male 0.0 0.0 35.0 United-States <=50K 32.0 Private 186824.0 HS-grad 9.0 Never-married Machine-op-inspct Unmarried White Male 0.0 0.0 40.0 United-States <=50K 38.0 Private 28887.0 11th 7.0 Married-civ-spouse Sales Husband White Male 0.0 0.0 50.0 United-States <=50K 43.0 Self-emp-not-inc 292175.0 Masters 14.0 Divorced Exec-managerial Unmarried White Female 0.0 0.0 45.0 United-States >50K 40.0 Private 193524.0 Doctorate 16.0 Married-civ-spouse Prof-specialty Husband White Male 0.0 0.0 60.0 United-States >50K 54.0 Private 302146.0 HS-grad 9.0 Separated Other-service Unmarried Black Female 0.0 0.0 20.0 United-States <=50K 35.0 Federal-gov 76845.0 9th 5.0 Married-civ-spouse Farming-fishing Husband Black Male 0.0 0.0 40.0 United-States <=50K 43.0 Private 117037.0 11th 7.0 Married-civ-spouse Transport-moving Husband White Male 0.0 2042.0 40.0 United-States <=50K 59.0 Private 109015.0 HS-grad 9.0 Divorced Tech-support Unmarried White Female 0.0 0.0 40.0 United-States <=50K 56.0 Local-gov 216851.0 Bachelors 13.0 Married-civ-spouse Tech-support Husband White Male 0.0 0.0 40.0 United-States >50K 19.0 Private 168294.0 HS-grad 9.0 Never-married Craft-repair Own-child White Male 0.0 0.0 40.0 United-States <=50K 54.0 ? 180211.0 Some-college 10.0 Married-civ-spouse ? Husband Asian-Pac-Islander Male 0.0 0.0 60.0 South >50K 39.0 Private 367260.0 HS-grad 9.0 Divorced Exec-managerial Not-in-family White Male 0.0 0.0 80.0 United-States <=50K 49.0 Private 193366.0 HS-grad 9.0 Married-civ-spouse Craft-repair Husband White Male 0.0 0.0 40.0 United-States <=50K 23.0 Local-gov 190709.0 Assoc-acdm 12.0 Never-married Protective-serv Not-in-family White Male 0.0 0.0 52.0 United-States <=50K 20.0 Private 266015.0 Some-college 10.0 Never-married Sales Own-child Black Male 0.0 0.0 44.0 United-States <=50K 45.0 Private 386940.0 Bachelors 13.0 Divorced Exec-managerial Own-child White Male 0.0 1408.0 40.0 United

We should perform a number of transformations before we can fit a machine learning model to our data. We will group these transformations in a pipeline. 

First, we should transform the categorical variables in our data set, as many machine learning algorithms can't handle categorical features. This can be done using one hot encoding, where we will basically create a new column for each category of the categorocal variable. 

We will use a combination of StringIndexer (to give every unique value in a column an index) and OneHotEncoderEstimator (to map the feature to a binary vector with at most a single one-value indicating the presence of a specific feature value from among the set of all feature values) to do so.

In [6]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import OneHotEncoderEstimator, StringIndexer, VectorAssembler

#These are all categorical columns that need to be transformed
categoricalColumns = ["workclass", "education", "marital_status", "occupation", "relationship", "race", "sex", "native_country"]

stages = [] # Here we will add the stages in our Pipeline
for categoricalCol in categoricalColumns:# Repeat this loop for each categorical column
    #Category Indexing with StringIndexer
    stringIndexer = StringIndexer(inputCol=categoricalCol, outputCol=categoricalCol + "Index")
    # Use OneHotEncoder to convert categorical variables into binary SparseVectors
    encoder = OneHotEncoderEstimator(inputCols=[stringIndexer.getOutputCol()], outputCols=[categoricalCol + "classVec"])
    # Add stages to the pipeline. These are not run here, but will run all at once later on.
    stages += [stringIndexer, encoder]
    

Next, we should also encode our labels to label indices as well. We can again use the StringIndexer to do so.

In [8]:
# Convert label into label indices using the StringIndexer
label_stringIdx = StringIndexer(inputCol="income", outputCol="label")
stages += [label_stringIdx]

Next, we should merge all feature columns into a single vector column. This is needed for machine learning algorithms to be applied.

In [10]:
# Transform all features into a vector using VectorAssembler
numericCols = ["age", "fnlwgt", "education_num", "capital_gain", "capital_loss", "hours_per_week"]
assemblerInputs = [c + "classVec" for c in categoricalColumns] + numericCols
assembler = VectorAssembler(inputCols=assemblerInputs, outputCol="features")
stages += [assembler]

Now, let's chain all the transformations together to specify our workflow in a pipeline

In [12]:
partialPipeline = Pipeline().setStages(stages)
pipelineModel = partialPipeline.fit(sparkdf)
preppedDataDF = pipelineModel.transform(sparkdf)

The only input data we need to fit a ML model, is the vector colomn with all the features and the label column. Let's select those two columns

In [14]:
selectedcols = ["label", "features"] 
dataset = preppedDataDF.select(selectedcols)
display(dataset)

label features 0.0 List(0, 100, List(1, 10, 23, 31, 43, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 50.0, 83311.0, 13.0, 13.0)) 0.0 List(0, 100, List(0, 8, 25, 38, 44, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 38.0, 215646.0, 9.0, 40.0)) 0.0 List(0, 100, List(0, 13, 23, 38, 43, 49, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 53.0, 234721.0, 7.0, 40.0)) 0.0 List(0, 100, List(0, 10, 23, 29, 47, 49, 62, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 28.0, 338409.0, 13.0, 40.0)) 0.0 List(0, 100, List(0, 11, 23, 31, 47, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 37.0, 284582.0, 14.0, 40.0)) 0.0 List(0, 100, List(0, 18, 28, 34, 44, 49, 64, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 49.0, 160187.0, 5.0, 16.0)) 1.0 List(0, 100, List(1, 8, 23, 31, 43, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 52.0, 209642.0, 9.0, 45.0)) 1.0 List(0, 100, List(0, 11, 24, 29, 44, 48, 53, 94, 95, 96, 97, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 31.0, 45781.0, 14.0, 14084.0, 50.0)) 1.0 List(0, 100, List(0, 10, 23, 31, 43, 48, 52, 53, 94, 95, 96, 97, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 42.0, 159449.0, 13.0, 5178.0, 40.0)) 1.0 List(0, 100, List(0, 9, 23, 31, 43, 49, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 37.0, 280464.0, 10.0, 80.0)) 1.0 List(0, 100, List(4, 10, 23, 29, 43, 50, 52, 61, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 30.0, 141297.0, 13.0, 40.0)) 0.0 List(0, 100, List(0, 10, 24, 32, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 23.0, 122272.0, 13.0, 30.0)) 0.0 List(0, 100, List(0, 14, 24, 33, 44, 49, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 32.0, 205019.0, 12.0, 50.0)) 1.0 List(0, 100, List(0, 12, 23, 30, 43, 50, 52, 55, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 40.0, 121772.0, 11.0, 40.0)) 0.0 List(0, 100, List(0, 16, 23, 37, 43, 51, 52, 54, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 34.0, 245487.0, 4.0, 45.0)) 0.0 List(0, 100, List(1, 8, 24, 39, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 25.0, 176756.0, 9.0, 35.0)) 0.0 List(0, 100, List(0, 8, 24, 35, 46, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 32.0, 186824.0, 9.0, 40.0)) 0.0 List(0, 100, List(0, 13, 23, 33, 43, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 38.0, 28887.0, 7.0, 50.0)) 1.0 List(0, 100, List(1, 11, 25, 31, 46, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 43.0, 292175.0, 14.0, 45.0)) 1.0 List(0, 100, List(0, 20, 23, 29, 43, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 40.0, 193524.0, 16.0, 60.0)) 0.0 List(0, 100, List(0, 8, 26, 34, 46, 49, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 54.0, 302146.0, 9.0, 20.0)) 0.0 List(0, 100, List(6, 18, 23, 39, 43, 49, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 35.0, 76845.0, 5.0, 40.0)) 0.0 List(0, 100, List(0, 13, 23, 37, 43, 48, 52, 53, 94, 95, 96, 98, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 43.0, 117037.0, 7.0, 2042.0, 40.0)) 0.0 List(0, 100, List(0, 8, 25, 40, 46, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 59.0, 109015.0, 9.0, 40.0)) 1.0 List(0, 100, List(2, 10, 23, 40, 43, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 56.0, 216851.0, 13.0, 40.0)) 0.0 List(0, 100, List(0, 8, 24, 30, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 19.0, 168294.0, 9.0, 40.0)) 1.0 List(0, 100, List(3, 9, 23, 36, 43, 50, 52, 65, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 54.0, 180211.0, 10.0, 60.0)) 0.0 List(0, 100, List(0, 8, 25, 31, 44, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 39.0, 367260.0, 9.0, 80.0)) 0.0 List(0, 100,

## Fitting the machine learning models
Before fitting a machine learning model, we should split our data in a training and test set. Then we can  set up the model and fit it on the training data.
Let's fit a logistic regression model, a decision tree and a random forest.

In [16]:
### Randomly split data into training and test sets. set seed for reproducibility
(trainingData, testData) = preppedDataDF.randomSplit([0.7, 0.3], seed=100)

from pyspark.ml.classification import LogisticRegression, DecisionTreeClassifier, RandomForestClassifier

# Create initial LogisticRegression model
lr = LogisticRegression(labelCol="label", featuresCol="features", maxIter=10)
dt = DecisionTreeClassifier(labelCol = 'label', featuresCol = 'features',  maxDepth = 3)
rf = RandomForestClassifier(featuresCol = 'features', labelCol = 'label', numTrees=100)

# Train model with Training Data
lrModel = lr.fit(trainingData)
dtModel = dt.fit(trainingData)

rfModel = rf.fit(trainingData)

In [17]:
# Make predictions on test data using the transform() method for the three models
predictions_LR = lrModel.transform(testData)
predictions_DT = dtModel.transform(testData)
predictions_RF = rfModel.transform(testData)


## Evaluating the models
Let's evaluate the three models in terms of their area under the ROC curve.

In [19]:
display(predictions_LR)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income workclassIndex workclassclassVec educationIndex educationclassVec marital_statusIndex marital_statusclassVec occupationIndex occupationclassVec relationshipIndex relationshipclassVec raceIndex raceclassVec sexIndex sexclassVec native_countryIndex native_countryclassVec label features rawPrediction probability prediction 17.0 ? 48703.0 11th 7.0 Never-married ? Own-child White Female 0.0 0.0 30.0 United-States <=50K 3.0 List(0, 8, List(3), List(1.0)) 5.0 List(0, 15, List(5), List(1.0)) 1.0 List(0, 6, List(1), List(1.0)) 7.0 List(0, 14, List(7), List(1.0)) 2.0 List(0, 5, List(2), List(1.0)) 0.0 List(0, 4, List(0), List(1.0)) 1.0 List(0, 1, List(), List()) 0.0 List(0, 41, List(0), List(1.0)) 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 48703.0, 7.0, 30.0)) List(1, 2, List(), List(8.361640192296251, -8.361640192296251)) List(1, 2, List(), List(0.999766393813901, 2.3360618609902863E-4)) 0.0 17.0 ? 67808.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United-States <=50K 3.0 List(0, 8, List(3), List(1.0)) 7.0 List(0, 15, List(7), List(1.0)) 1.0 List(0, 6, List(1), List(1.0)) 7.0 List(0, 14, List(7), List(1.0)) 2.0 List(0, 5, List(2), List(1.0)) 0.0 List(0, 4, List(0), List(1.0)) 0.0 List(0, 1, List(0), List(1.0)) 0.0 List(0, 41, List(0), List(1.0)) 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 67808.0, 6.0, 40.0)) List(1, 2, List(), List(7.666454361904844, -7.666454361904844)) List(1, 2, List(), List(0.999531943960885, 4.6805603911499803E-4)) 0.0 17.0 ? 80077.0 11th 7.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United-States <=50K 3.0 List(0, 8, List(3), List(1.0)) 5.0 List(0, 15, List(5), List(1.0)) 1.0 List(0, 6, List(1), List(1.0)) 7.0 List(0, 14, List(7), List(1.0)) 2.0 List(0, 5, List(2), List(1.0)) 0.0 List(0, 4, List(0), List(1.0)) 1.0 List(0, 1, List(), List()) 0.0 List(0, 41, List(0), List(1.0)) 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 80077.0, 7.0, 20.0)) List(1, 2, List(), List(8.684617598867284, -8.684617598867284)) List(1, 2, List(), List(0.9998308605021862, 1.6913949781383598E-4)) 0.0 17.0 ? 86786.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United-States <=50K 3.0 List(0, 8, List(3), List(1.0)) 7.0 List(0, 15, List(7), List(1.0)) 1.0 List(0, 6, List(1), List(1.0)) 7.0 List(0, 14, List(7), List(1.0)) 2.0 List(0, 5, List(2), List(1.0)) 0.0 List(0, 4, List(0), List(1.0)) 1.0 List(0, 1, List(), List()) 0.0 List(0, 41, List(0), List(1.0)) 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 86786.0, 6.0, 40.0)) List(1, 2, List(), List(8.220432560972577, -8.220432560972577)) List(1, 2, List(), List(0.9997309737564378, 2.690262435622275E-4)) 0.0 17.0 ? 112942.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United-States <=50K 3.0 List(0, 8, List(3), List(1.0)) 7.0 List(0, 15, List(7), List(1.0)) 1.0 List(0, 6, List(1), List(1.0)) 7.0 List(0, 14, List(7), List(1.0)) 2.0 List(0, 5, List(2), List(1.0)) 0.0 List(0, 4, List(0), List(1.0)) 0.0 List(0, 1, List(0), List(1.0)) 0.0 List(0, 41, List(0), List(1.0)) 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 112942.0, 6.0, 40.0)) List(1, 2, List(), List(7.610679099376499, -7.610679099376499)) List(1, 2, List(), List(0.9995051095397631, 4.948904602367223E-4)) 0.0 17.0 ? 138507.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 20.0 United-States <=50K 3.0 List(0, 8, List(3), List(1.0)) 7.0 List(0, 15, List(7), List(1.0)) 1.0 List(0, 6, List(1), List(1.0)) 7.0 List(0, 14, List(7), List(1.0)) 2.0 List(0, 5, List(2), List(1.0)) 0.0 List(0

In [20]:
from pyspark.ml.evaluation import BinaryClassificationEvaluator
# Evaluate model
evaluator = BinaryClassificationEvaluator(rawPredictionCol="rawPrediction")
print(evaluator.evaluate(predictions_LR))
print(evaluator.evaluate(predictions_DT))
print(evaluator.evaluate(predictions_RF))


0.9032867661805299
0.7390076784230583
0.8889524969200399